# __WSI - ćwiczenie 6.__

### __Uczenie się ze wzmocnieniem__

#### __Treść ćwiczenia__

- Celem ćwiczenia jest implementacja algorytmu Q-learning. 
- Następnie należystworzyć agenta rozwiązującego problem Taxi. 
- Problem dostępny jest w pakieciegym(gym.make(’Taxi-v3’))

In [169]:
import numpy as np
import pandas as pd
import gymnasium as gym
from IPython.display import clear_output
from time import sleep 
RNG = np.random.default_rng()
import plotly.express as px

In [170]:
env = gym.make('Taxi-v3', render_mode='ansi').env

In [171]:
class Agent():
    def __init__(self, state_space_size, 
                       action_space_size, 
                       learning_rate,
                       discount_factor,
                       exploration_coef) -> None:
        # self._state_space_size = state_space_size
        # self._action_space_size = action_space_size
        self._learning_rate = learning_rate
        self._discount_factor = discount_factor
        self._exploration_coef = exploration_coef
        self._q_table = np.zeros((state_space_size, action_space_size))

    def greedy_action(self, state):
        return np.argmax(self._q_table[state])

    def random_action(self, state):
        return RNG.choice(np.array(range(self._q_table.shape[1])))

    def action(self, state):
        if RNG.uniform() > self._exploration_coef:
            return self.greedy_action(state)
        return self.random_action(state)

    def update(self, prev_state, curr_state, prev_action, reward):
        prev_q = self._q_table[prev_state, prev_action]
        curr_max_q = np.max(self._q_table[curr_state])
        delta = reward + self._discount_factor * curr_max_q - prev_q
        self._q_table[prev_state, prev_action] = prev_q + self._learning_rate * delta

1. learning rate
2. współczynnik dyskontowania
3. współczynnik eksploracji
4. ilość epok w funkcji czasu

In [172]:
agent = Agent(env.observation_space.n, env.action_space.n, 0.1, 0.6, 0.1)
num_episodes  = 10000
episode_step_limit =  1000
train_steps_per_episode = []
train_reward_per_episode = [] 
for episode in range(num_episodes):
    curr_state, info = env.reset()
    terminated, truncated = False, False
    steps = 0
    reward_sum = 0
    while not (terminated or truncated or steps > episode_step_limit):
        action = agent.action(curr_state)
        prev_state = curr_state
        curr_state, reward, terminated, truncated, info = env.step(action)
        agent.update(prev_state, curr_state, action, reward)
        steps += 1
        reward_sum += reward
    train_steps_per_episode.append(steps)
    train_reward_per_episode.append(reward_sum)

env.close()

C:\Users\filip\AppData\Local\Programs\Python\Python311\Lib\site-packages\gymnasium\utils\passive_env_checker.py:249: DeprecationWarning:

`np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)



In [173]:
px.line(x=range(len(train_reward_per_episode)),  y=train_reward_per_episode)

In [174]:
px.line(x=range(len(train_steps_per_episode)),  y=train_steps_per_episode)

learning rate


In [175]:
learn_rates = np.geomspace(0.05, 1, 10)
training_outcomes = []
for val in learn_rates:
    agent = Agent(env.observation_space.n, env.action_space.n, val, 0.6, 0.1)
    num_episodes  = 10000
    episode_step_limit =  1000
    train_steps_per_episode = []
    for episode in range(num_episodes):
        curr_state, info = env.reset()
        terminated, truncated = False, False
        steps = 0
        while not (terminated or truncated or steps > episode_step_limit):
            action = agent.action(curr_state)
            prev_state = curr_state
            curr_state, reward, terminated, truncated, info = env.step(action)
            agent.update(prev_state, curr_state, action, reward)
            steps += 1
        train_steps_per_episode.append(steps)
    training_outcomes.append(train_steps_per_episode)

env.close()

In [176]:
learn_rates = pd.DataFrame(np.array(training_outcomes).T, columns=learn_rates)

In [177]:
px.line(learn_rates)

dicsount coefficient

In [178]:
discounts = np.geomspace(0.05, 1, 10)
training_outcomes = []
for val in discounts:
    agent = Agent(env.observation_space.n, env.action_space.n, 1, 0.6, 0.1)
    num_episodes  = 10000
    episode_step_limit =  1000
    train_steps_per_episode = []
    for episode in range(num_episodes):
        curr_state, info = env.reset()
        terminated, truncated = False, False
        steps = 0
        while not (terminated or truncated or steps > episode_step_limit):
            action = agent.action(curr_state)
            prev_state = curr_state
            curr_state, reward, terminated, truncated, info = env.step(action)
            agent.update(prev_state, curr_state, action, reward)
            steps += 1
        train_steps_per_episode.append(steps)
    training_outcomes.append(train_steps_per_episode)

env.close()

In [179]:
discounts = pd.DataFrame(np.array(training_outcomes).T, columns=discounts) 

In [180]:
px.line(discounts)

In [181]:
agent = Agent(env.observation_space.n, env.action_space.n, 0.1, 0.6, 0.1)
num_episodes  = 50000
episode_step_limit =  1000
train_steps_per_episode = []
train_reward_per_episode = [] 
for episode in range(num_episodes):
    curr_state, info = env.reset()
    terminated, truncated = False, False
    steps = 0
    reward_sum = 0
    while not (terminated or truncated or steps > episode_step_limit):
        action = agent.action(curr_state)
        prev_state = curr_state
        curr_state, reward, terminated, truncated, info = env.step(action)
        agent.update(prev_state, curr_state, action, reward)
        steps += 1
        reward_sum += reward
    train_steps_per_episode.append(steps)
    train_reward_per_episode.append(reward_sum)

env.close()

In [ ]:
test_steps_per_episode = []
test_reward_per_episode = [] 
num_episodes = 100
for episode in range(num_episodes):
    steps =  0
    reward_sum = 0
    curr_state, info = env.reset()
    action_mask = info['action_mask']
    terminated, truncated = False, False
    while not terminated or truncated:
        action = agent.action(curr_state)
        curr_state, reward, terminated, truncated, info = env.step(action)
        steps += 1
        reward_sum += reward
    test_steps_per_episode.append(steps)
    test_reward_per_episode.append(reward_sum)
env.close()
avg_steps = np.mean(test_steps_per_episode)
avg_reward = np.mean(test_reward_per_episode)
print(avg_steps, avg_reward)

18.53 -2.66


Agent potrzebuje kilkudziesięciu tysięcy epizodów żeby tabela stanów ustabilizowała się w okolicy lokalnego minimum 